# cdasws and hdpws Example Jupyter Notebook
![SPASE inside](https://spase-group.org/assets/images/spase-inside.png)
This [Jupyter notebook](https://jupyter.org/) demonstrates using the [cdasws](https://pypi.org/project/cdasws/) and [hdpws](https://pypi.org/project/hdpws/) Python packages to obtain [uri-template](https://github.com/hapi-server/uri-templates) values for [CDAWeb](https://cdaweb.gsfc.nasa.gov/) datasets.  It assumes some familarity with the [SPASE data model](https://spase-group.org/data/index.html).  This notebook contains the following sections:
1. [Prerequisites](#Prerequisites)
1. [Setup](#Setup)
1. [Get CDAWeb Dataset Descriptions](#Get-CDAWeb-Dataset-Descriptions)
1. [Additional Documentation](#Additional-Documentation)

## Prerequisites
Install the prerequisite software from [Python Package Index](https://pypi.org/) (PyPI) software repository.
1. pip install hdpws
1. pip install cdasws

## Setup
Execute some preliminary code that is necessary before the code that follows.

In [1]:
from hdpws.hdpws import HdpWs
from hdpws import NAMESPACES as NS
from hdpws.spase import AccessURL

from cdasws import CdasWs

from IPython.display import HTML


hdp = HdpWs()
cdas = CdasWs()

## Get CDAWeb Dataset Descriptions
The following code gets descriptions of all [CDAWeb](https://cdaweb.gsfc.nasa.gov/) datasets.  Then for each dataset, it obtains and prints the corrsponding `AccessDirectoryTemplate` and `AccessFilenameTemplate` from [HDP](https://heliophysicsdata.gsfc.nasa.gov).

In [2]:
dataset_descriptions = cdas.get_datasets()
html = '<table><caption>CDAWeb Datasets</caption><tr><th>Identifier</th><th>Directory Template</th><th>Filename Template</th></tr>'
for dataset in dataset_descriptions[0:9]:
    identifier = dataset['Id']
    if 'SpaseResourceId' in dataset:
        spase_id = dataset['SpaseResourceId']
        result = hdp.get_spase([spase_id])
        if result['HttpStatus'] == 200:
            spase = result['Result'].findall('.//Spase', namespaces=NS)[0]
            cdaweb_access_information = \
                spase.find('.//AccessURL[Name="CDAWeb"]/..', namespaces=NS)
            if cdaweb_access_information is not None:
                dir_template = cdaweb_access_information.find('./AccessDirectoryTemplate',
                                              namespaces=NS)
                file_template = cdaweb_access_information.find('./AccessFilenameTemplate',
                                              namespaces=NS)
                if dir_template is not None and file_template is not None:
                    #print(f'{identifier} "{dir_template.text}" {file_template.text}')
                    html += f'<tr><td>{identifier}</td><td><pre>{dir_template.text}</pre></td><td><pre>{file_template.text}<pre></td></tr>'
                else:
                    print(f'failed to find templates for {spase_id}')
                    print(cdaweb_access_information)
            else:
                print(f'failed to find cdaweb access information for {spase_id}')
        else:
            print(f'failed to get spase for {spase_id}')
html += '</table>'
display(HTML(html))
        

## Additional Documentation
View the [hdpws](https://heliophysicsdata.gsfc.nasa.gov/WebServices/py/hdpws/) and [cdasws](https://cdaweb.gsfc.nasa.gov/WebServices/REST/py/cdasws/) API documentation for a description of additional features.